In [17]:
import pandas as pd
import folium, branca
from folium.plugins import TimestampedGeoJson
from folium import Popup
from bs4 import BeautifulSoup
import requests
from datetime import datetime
from urllib.error import HTTPError

In [20]:
dates = pd.date_range(start='01-22-2020', end = datetime.now()).to_list()

In [23]:
df = pd.DataFrame()

In [24]:
for date in dates:
    date_str = date.strftime('%m-%d-%Y')
    path = f'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/{date_str}.csv'
    try:
        download_df = pd.read_csv(path)
        df = df.append(download_df)
    except HTTPError as e:
        pass

In [230]:
df0 = df.copy()

In [236]:
df0['province_country'] = df0['Province/State'].str.cat(df0['Country/Region'], na_rep = '')

In [239]:
df_max = df0.groupby('province_country')[['Latitude','Longitude']].max().reset_index()

In [240]:
df1 = pd.merge(df0, df_max, how = 'left', on = 'province_country')

In [267]:
df1['Latitude'] = df1['Latitude_x'].fillna(df1['Latitude_y'])
df1['Longitude'] = df1['Longitude_x'].fillna(df1['Longitude_y'])

In [268]:
df2 = df1[df1['Latitude'].notnull() & df1['Longitude'].notnull()].copy()

In [269]:
df2['Last Update Date'] = pd.to_datetime(df2['Last Update'], yearfirst=True)

In [270]:
location = (43.0000,12.0000)

In [271]:
df3 = df2[(df2['Confirmed']>0)|(df2['Deaths']>0)|(df2['Recovered']>0)].copy()

In [344]:
colormap_confirmed = branca.colormap.linear.YlOrRd_03.scale(0, df3['Confirmed'].max())
colormap_deaths = branca.colormap.LinearColormap(['#9fc8e1','#2171b5']).scale(0, df3['Deaths'].max())
colormap_recovered = branca.colormap.linear.RdYlGn_03.scale(0, df3['Recovered'].max())

In [366]:
features_confirmed = []

In [367]:
for _, row in df3[df3['Confirmed']>0].sort_values('Confirmed').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_confirmed(row['Confirmed'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_confirmed(row['Confirmed']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            }
        }
    }
    features_confirmed.append(feature)

In [368]:
features_deaths = []

In [369]:
for _, row in df3[df3['Deaths']>0].sort_values('Deaths').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_deaths(row['Deaths'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_deaths(row['Deaths']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            }
        }
    }
    features_deaths.append(feature)

In [370]:
features_recovered = []

In [371]:
for _, row in df3[df3['Recovered']>0].sort_values('Recovered').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_recovered(row['Recovered'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_recovered(row['Recovered']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            }
        }
    }
    features_recovered.append(feature)

In [372]:
# Initialize the map object and add the colorbar at the top
fm_confirmed = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=1000, height=400)\
.add_child(colormap_confirmed)

In [373]:
# Initialize the map object and add the colorbar at the top
fm_deaths = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=1000, height=400)\
.add_child(colormap_deaths)

In [374]:
fm_recovered = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=1000, height=400)\
.add_child(colormap_recovered)

In [375]:
# Initialize the TimestampedGeoJson object and add to map
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_confirmed}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1D'
).add_to(fm_confirmed)

In [376]:
# Initialize the TimestampedGeoJson object and add to map
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_deaths}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1D'
).add_to(fm_deaths)

In [377]:
# Initialize the TimestampedGeoJson object and add to map
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_recovered}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1D'
).add_to(fm_recovered)

In [378]:
fm_confirmed

In [379]:
fm_deaths

In [380]:
fm_recovered